In [25]:
#import
import nltk
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from nltk.stem import PorterStemmer
from nltk.stem import WordNetLemmatizer
import pandas as pd
import regex as re

nltk.download('punkt')
nltk.download('stopwords')
nltk.download('wordnet')

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\HP\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\HP\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\HP\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


True

In [26]:
import scrapy
from scrapy.crawler import CrawlerProcess
import json

class HealthSpider(scrapy.Spider):
    name = 'health'
    start_urls = ['https://www.webteb.com/diseases']

    def parse(self, response):
        items = response.css('div.content.acc-content ul.list li')
        for item in items:
            disease_type = item.css('a::text').get().strip()
            disease_link = item.css('a::attr(href)').get()
            base_link = disease_link.split('/diseases')[0]
            full_link = response.urljoin(base_link + "/diseases/")
            yield scrapy.Request(url=full_link, callback=self.parse_disease_list, meta={'disease_type': disease_type, 'link': full_link})

    def parse_disease_list(self, response):
        disease_type = response.meta['disease_type']
        diseases = response.css('div.search-result.border div.content')
        for disease in diseases:
            disease_name = disease.css('a.bold span::text').get().strip()
            disease_link = disease.css('a.bold::attr(href)').get()
            full_disease_link = response.urljoin(disease_link)
            yield scrapy.Request(url=full_disease_link, callback=self.parse_disease_details, meta={'disease_type': disease_type, 'disease_name': disease_name})

    def parse_disease_details(self, response):
        disease_type = response.meta['disease_type']
        disease_name = response.meta['disease_name']
        
        # Extracting data for each section
        description = response.css('div#description').xpath('string()').get().strip()
        symptoms_title = response.css('div#symptoms > h2::text').get()
        symptoms = '\n'.join(response.css('div#symptoms ul li::text').getall())
        causes_and_risk_factors_title = response.css('div#causesandriskfactors > h2::text').get()
        causes_and_risk_factors = '\n'.join(response.css('div#causesandriskfactors ul li::text').getall())
        complications_title = response.css('div#complications > h2::text').get()
        complications = '\n'.join(response.css('div#complications ul li::text').getall())
        diagnosis_title = response.css('div#diagnosis > h2::text').get()
        diagnosis = '\n'.join(response.css('div#diagnosis ul li::text').getall())
        treatments_and_drugs_title = response.css('div#treatementsanddrugs > h2::text').get()
        treatments_and_drugs = '\n'.join(response.css('div#treatementsanddrugs p::text').getall())
        prevention_title = response.css('div#prevention > h2::text').get()
        prevention = '\n'.join(response.css('div#prevention ul li::text').getall())

        content = f"{disease_type}\n{disease_name}\n{description}\n\n{symptoms_title}:\n{symptoms}\n\n{causes_and_risk_factors_title}:\n{causes_and_risk_factors}\n\n{complications_title}:\n{complications}\n\n{diagnosis_title}:\n{diagnosis}\n\n{treatments_and_drugs_title}:\n{treatments_and_drugs}\n\n{prevention_title}:\n{prevention}"

        yield {
            'disease_type': disease_type,
            'disease_name': disease_name,
            'content': content
        }


# Create a process to run the spider
process = CrawlerProcess(settings={
    'FEEDS': {
        'disease_details2.json': {
            'format': 'json',
            'encoding': 'utf8',
            'overwrite': True,
        },
    },
})

# Run the spider
process.crawl(HealthSpider)
process.start()

# Load and display the data from the JSON file
with open('disease_details2.json', 'r', encoding='utf8') as f:
    disease_details = json.load(f)

# Display the extracted data
for item in disease_details:
    print(item['content'])


2024-05-27 09:57:35 [scrapy.utils.log] INFO: Scrapy 2.8.0 started (bot: scrapybot)
2024-05-27 09:57:35 [scrapy.utils.log] INFO: Versions: lxml 4.9.3.0, libxml2 2.10.4, cssselect 1.1.0, parsel 1.6.0, w3lib 1.21.0, Twisted 22.10.0, Python 3.11.5 | packaged by Anaconda, Inc. | (main, Sep 11 2023, 13:26:23) [MSC v.1916 64 bit (AMD64)], pyOpenSSL 23.2.0 (OpenSSL 3.0.13 30 Jan 2024), cryptography 41.0.3, Platform Windows-10-10.0.19045-SP0
2024-05-27 09:57:35 [scrapy.crawler] INFO: Overridden settings:
{}
2024-05-27 09:57:35 [py.warnings] WARNING: C:\Users\HP\anaconda3\Lib\site-packages\scrapy\utils\request.py:232: ScrapyDeprecationWarning: '2.6' is a deprecated value for the 'REQUEST_FINGERPRINTER_IMPLEMENTATION' setting.

It is also the default value. In other words, it is normal to get this warning if you have not defined a value for the 'REQUEST_FINGERPRINTER_IMPLEMENTATION' setting. This is so for backward compatibility reasons, but it will change in a future version of Scrapy.

See the 

2024-05-27 09:57:39 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.webteb.com/dental-health/diseases/%D8%A7%D9%85%D8%B1%D8%A7%D8%B6-%D8%A7%D9%84%D8%AA%D9%87%D8%A7%D8%A8-%D8%A7%D9%84%D9%84%D8%A8>
{'disease_type': 'تسوس الأسنان', 'disease_name': 'امراض التهاب اللب', 'content': 'تسوس الأسنان\nامراض التهاب اللب\nقد يكون الالتهاب المتكون في لّب السن بفعل التلوث الجرثومي جزئيًا، وفي مثل هذه الحالات يكون قابلًا للعكس (Reversible) وقابلًا للإصلاح.\r\n\r\nيقدم طبيب الأسنان علاجات تحفظية، مثل: حشو لب السن، أو مينا السن دون الحاجة إلى إخراج اللّب المصاب بالالتهاب، بل حتى دون الحاجة إلى معالجة قناة جذر السن.\r\n\r\nأما في الحالات الأخرى غير القابلة للإصلاح، مثل: التهاب اللب المزمن، والتهاب اللّب الحاد، وموت الأنسجة\xa0في اللّب، فإن الطبيب لا يستطيع معالجة الالتهاب بواسطة الأدوية بغاية إعادة السن إلى سابق عهده وإنما يتوجب عليه إخراج اللّب المصاب بالالتهاب ومعالجة قناة جذر السن.\r\n\r\nوظائف لب السن\r\n\r\nيُعد نسيج اللبّ النسيج اللين الوحيد في السن وهو موجود في الجزء الداخلي من جذر السن

2024-05-27 09:57:39 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.webteb.com/cancer/diseases/%D8%B3%D8%A7%D8%B1%D9%83%D9%88%D9%85%D8%A9-%D9%83%D8%A7%D8%A8%D9%88%D8%B2%D9%8A>
{'disease_type': 'تسوس الأسنان', 'disease_name': 'ساركوما كابوزي', 'content': 'تسوس الأسنان\nساركوما كابوزي\nساركوما كابوزي عبارة عن عملية تكاثر متعددة البؤر مصدرها من البطائن (Endothelium) وقد وصفها موريس كابوزي في العام 1872 بأنها آفة ساركومة كابوزي تظهر كوصمة، أو طبقة، أو عقدة وورم، وبلون وردي حتى بنفسجي وبأشكال وأحجام مختلفة.\r\n\r\nيختلف عدد الآفات لدى المريض وهي تظهر في كل مكان من جلد الجسم وخاصة في أطراف الأعضاء، تتوزع الآفات في كل أجزاء الجسم أو تتمركز في منطقة معينة مثل الأطراف السفلية.\xa0\r\n\r\nتتمركز التغييرات المجهرية المترتبة عن ساركوما كابوزي في الأدمة الشبكية (Reticular dermis) ثم تنفذ تدريجيًا إلى عمق الأدمة وهي تتميز بخليط من الخلايا المغزليّة (Spindle cell) وتكاثر خلايا بطانية في داخل شبكة من الألياف الشبكية والكولاجين مع فراغات بطانية بين الخلايا المغزليّة.\r\n\r\nوجود كريات دم حمر

2024-05-27 09:57:39 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.webteb.com/healthy-beauty/diseases/%D8%AD%D8%A8-%D8%A7%D9%84%D8%B4%D8%A8%D8%A7%D8%A8>
{'disease_type': 'حب الشباب', 'disease_name': 'حب الشباب', 'content': 'حب الشباب\nحب الشباب\nحب الشباب\xa0قد يشكل مصدر إزعاج يومي دائم، فالشفاء من حب الشباب يتم ببطء فما أن تبدأ بالاختفاء حتى تظهر أخرى غيرها كانت في الانتظار، هذه المعركة المستمرّة واللامتناهية تتكرّر مرارًا بصورة متعبة ومثيرة لليأس.\r\n\r\nمن المرجّح أنّ للهرمونات دورًا رئيسًا في ظهور حب الشباب وجعلها مصدر إزعاج لدى الشباب على وجه الخصوص، مع ذلك قد يُعاني النّاس من كل الفئات العمريّة منه.\r\n\r\nكما قد تعاني بعض النساء من ظهور حب الشباب باعتدال في مراحل مختلفة من التغييرات الهرمونيّة التي تتخلّل حياتها، مثل: فترة الحمل، والدورة الشهرية، وعند استعمال الحبوب المانعة للحمل أو عند التوقف عن تناولها.\n\nأعراض حب الشباب:\n\n\nأسباب وعوامل خطر حب الشباب:\nإنتاج فائض من الزّهْم.\nتشكل غير منتظم لخلايا الجلد الميّتة يتسبب في تنبيه بصيلات الشعر في الجلد.\nتراكم \n.\n

2024-05-27 09:57:39 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://www.webteb.com/integumentary-system/diseases/%D8%AA%D8%B3%D8%A7%D9%82%D8%B7-%D8%A7%D9%84%D8%B4%D8%B9%D8%B1> (referer: https://www.webteb.com/integumentary-system/diseases/)
2024-05-27 09:57:39 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://www.webteb.com/gastrointestinal-tract/diseases/%D9%85%D8%B1%D8%B6-%D9%83%D8%B1%D9%88%D9%86> (referer: https://www.webteb.com/general-health/diseases/)
2024-05-27 09:57:39 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://www.webteb.com/child-health/diseases/%D9%85%D8%AA%D9%84%D8%A7%D8%B2%D9%85%D8%A9-%D8%AF%D8%A7%D9%88%D9%86> (referer: https://www.webteb.com/general-health/diseases/)
2024-05-27 09:57:39 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://www.webteb.com/dermatology/diseases/%D8%A7%D9%83%D8%B2%D9%8A%D9%85%D9%87> (referer: https://www.webteb.com/general-health/diseases/)
2024-05-27 09:57:39 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://www

...

2024-05-27 09:58:48 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.webteb.com/respiratory/diseases/%D8%B3%D8%AD%D8%A7%D8%B1-%D9%82%D8%B7%D9%86%D9%8A-%D8%B3%D8%AD%D8%A7%D8%B1-%D8%A7%D9%84%D8%AD%D9%84%D8%A7%D8%AC%D9%8A%D9%86>
{'disease_type': 'الجهاز التنفسي', 'disease_name': 'السحار القطني', 'content': 'الجهاز التنفسي\nالسحار القطني\nالسحار القطني هو مرض انسدادي مزمن في المسالك الهوائية التنفسية، قد يتولد ويتطور لدى العمال المعرضين لغبار القطن، والكتان، وأنواع أخرى من النسيج، فهو مرض رئوي نادر وهو ناتج عن استنشاق جزيئات القنب والكتان والقطن ويشار إليه أحيانًا بمرض الرئة البني، حيث أنه شكل من أشكال الربو المهني.\r\n\r\nيؤدي هذا المرض إلى انسداد أنابيب الهواء الصغيرة التي تسمى القصيبات، لذلك يمكن أن يسبب أعراضًا مثل الربو أو تلفًا دائمًا في الرئة مشابهًا لمرض الانسداد الرئوي المزمن.\r\n\r\nالعمال العاملون في المعالجة الأولية للقطن الخام أكثر عرضة للإصابة بهذا المرض من الأشخاص الآخرين، وفي المرحلة الصعبة من المرض يطرأ انخفاض ثابت في قدرة الرئتين على التنفس.\n\nأعراض السحار القط

2024-05-27 09:58:48 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.webteb.com/respiratory/diseases/%D8%A7%D9%84%D8%B3%D8%AD%D8%A7%D8%B1-%D8%A7%D9%84%D8%B3%D9%8A%D9%84%D9%8A%D8%B3%D9%8A>
{'disease_type': 'الجهاز التنفسي', 'disease_name': 'السحار السيليسي', 'content': 'الجهاز التنفسي\nالسحار السيليسي\nالسحار السيليسيّ هو مرض رئوي ينشأ بسبب استنشاق جزيئات غبار سيليكا حرة أي ثاني أكسيد السيلسيوم (SiO2)، حيث تدخل هذه البلورات إلى الحويصلات الهوائية، وهناك يتم ابتلاعها من قبل خلايا البلعمة (Macrophages) الموجودة في الجدار والنسيج الخلالي (Interstitial tissue).\r\n\r\nتفكيك الحويصلات الهوائية هو الأساس لتكون ونشوء هذا المرض، فنتيجة لتلف الخلايا تُطلق إلى النسيج مواد جاذبة كيميائيًا (Chemotactic) تؤدي إلى تحفيز خلايا الأرومة الليفية إلى رد فعل التهابي، وتغيرات تليفية في النسيج الأوسط، وظهور العقيدات السيليسية (Silicotic nodule).\r\n\r\nهذه العقيدات تنمو وفيما بعد تمتزج لتكوّن كتلًا يبلغ قطر الواحدة منها بضع سنتيمتر، حيث تتطور هذه العملية تدريجيًا بعد عدة سنين من التعرض لغبار السيلي

2024-05-27 09:58:48 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.webteb.com/respiratory/diseases/%D8%A7%D9%84%D8%B1%D8%A8%D9%88-%D8%B9%D9%86%D8%AF-%D8%A7%D9%84%D8%A7%D8%B7%D9%81%D8%A7%D9%84>
{'disease_type': 'الجهاز التنفسي', 'disease_name': 'الربو عند الاطفال', 'content': 'الجهاز التنفسي\nالربو عند الاطفال\nيعد\xa0الربو\xa0أحد الأمراض التي تصيب القصبات الهوائية التي توصل الهواء من وإلى الرئتين، وعادةً ما يظهر عند الأطفال مع إمكانية ظهوره في أية عمر آخر.\r\n\r\nتختلف آلية تطور المرض من شخص لآخر، إذ تختفي نوبات ضيق النفس بعد انتهاء مرحلة الطفولة عند معظم الأشخاص بينما تستمر عند مجموعة أخرى لفترات طويلة.\r\n\r\nفي الفترة الأخيرة كان هناك ازدياد ملحوظ في أعداد مرضى الربو، وقد يرجع ذلك إلى ازدياد العوامل المحفزة لحدوث المرض، مثل ارتفاع جودة النظافة والصرف الصحي (Sanitation)، وتقلص عدد الأولاد في العائلة.\r\n\r\nيندر إصابة كبار العمر وفي مثل هذه الحالة لا يمكن تحديد العامل المسبب للربو، ويحتاج المريض إلى كميات كبيرة من الأدوية للسيطرة على الحالة.\n\nأعراض الربو عند الأطفال:\nن

2024-05-27 09:58:48 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.webteb.com/respiratory/diseases/%D8%A7%D9%84%D8%B1%D8%A8%D9%88>
{'disease_type': 'الجهاز التنفسي', 'disease_name': 'الربو', 'content': 'الجهاز التنفسي\nالربو\nالربو هو مرض مزمن يصيب الإنسان نتيجة التهاب مجاري الهواء في الرئتين أو الشّـُعَب الهوائية وتضيقهما، الأمر الذي يُقلل أو يمنع من تدفق الهواء إلى هذه الشعب مسببًا نوبات متكررة من ضيق التنفس التي يرافقها صفير بمنطقة الصدر وبعض الأعراض الأخرى.\r\n\r\nحيث تنقبض العضلة التي تحيط بالشعب الهوائية وتتراكم كمية كبيرة من البلغم في مجاري الهواء مما يؤدي إلى انسدادها، لتتراوح وفقًا لذلك أعراض الإصابة بالربو بين الخشخشة والصفير الخفيفين عند التنفس وبين نوبات ربو قد تعرض الحياة للخطر، علمًا أن الأطفال أكثر إصابةً بالمرض.\r\n\r\nليس هنالك علاج لمرض الربو لكن من الممكن السيطرة على أعراضه باتباع طرق مختلفة.\r\n\r\nإذا لم يكن الربو تحت المراقبة والمتابعة فقد يسبب التغيب المتكرر والطويل عن المدرسة أو عن العمل مما قد يُقلّص مستوى الإنتاجية، تتغير حدة الربو مع الوقت لدى معظ

2024-05-27 09:58:49 [scrapy.core.engine] INFO: Closing spider (finished)
2024-05-27 09:58:49 [scrapy.extensions.feedexport] INFO: Stored json feed (1130 items) in: disease_details2.json
2024-05-27 09:58:49 [scrapy.statscollectors] INFO: Dumping Scrapy stats:
{'downloader/request_bytes': 549585,
 'downloader/request_count': 1186,
 'downloader/request_method_count/GET': 1186,
 'downloader/response_bytes': 97893759,
 'downloader/response_count': 1186,
 'downloader/response_status_count/200': 1168,
 'downloader/response_status_count/302': 16,
 'downloader/response_status_count/404': 2,
 'dupefilter/filtered': 515,
 'elapsed_time_seconds': 72.594695,
 'feedexport/success_count/FileFeedStorage': 1,
 'finish_reason': 'finished',
 'finish_time': datetime.datetime(2024, 5, 27, 8, 58, 49, 39969),
 'httpcompression/response_bytes': 353842916,
 'httpcompression/response_count': 1169,
 'httperror/response_ignored_count': 2,
 'httperror/response_ignored_status_count/404': 2,
 'item_scraped_count': 1

In [46]:
import pandas as pd
import json

# Load your JSON data with utf-8 encoding
with open('disease_details1.json', 'r', encoding='utf-8') as json_file:
    data = json.load(json_file)

# Create a DataFrame
df = pd.DataFrame(data)

# Add an empty column named "score"
df = df.assign(score='')

# Display the first few rows
df.head()

disease_type                 disease_name  \
0  تسوس الأسنان  امراض الاغشية المخاطية للفم   
1  تسوس الأسنان            امراض التهاب اللب   
2  تسوس الأسنان         عيوب خلقية لجوف الفم   
3    مرض السكري             حساسية الإنسولين   
4  تسوس الأسنان               ساركوما كابوزي   

                                             content score  
0  تسوس الأسنان\nامراض الاغشية المخاطية للفم\nتغط...        
1  تسوس الأسنان\nامراض التهاب اللب\nقد يكون الالت...        
2  تسوس الأسنان\nعيوب خلقية لجوف الفم\nيوجد للفم ...        
3  مرض السكري\nحساسية الإنسولين\nحتى نهاية سنوات ...        
4  تسوس الأسنان\nساركوما كابوزي\nساركوما كابوزي ع...

In [47]:
import pandas as pd
import json

# Define the score_text function
def score_text(text):
    # Define your scoring rules here
    score = 0
    
    # Keywords related to symptoms
    symptoms_keywords = ['ألم', 'عرض', 'علامة', 'ظهور', 'تشعر', 'تشعرين', 'يشعر', 'يعاني', 'يعانون', 'يعاني من', 'يعانون من', 'أعراض جانبية', 'تأثيرات جانبية', 'تغييرات في الجسم', 'وظائف غير طبيعية', 'مشاكل صحية', 'انزعاج', 'إزعاج', 'وجه', 'رأس', 'رقبة', 'صدر', 'ظهر', 'بطن', 'ذراع', 'ساق', 'مفصل', 'عضلة', 'جلد', 'شعر', 'أظافر', 'فم', 'لسان', 'أسنان', 'لثة', 'عيون', 'أذنين', 'أنف', 'شديد', 'حاد', 'خفيف', 'متوسط', 'مستمر', 'متقطع', 'مزمن', 'لا يطاق', 'غير محتمل', 'مُنهِك', 'مُؤلم', 'يُعيق', 'يُضعف', 'يُسبب إعاقة', 'حرقة', 'وخز', 'خدر', 'حكة', 'ألم غامض', 'ضعف', 'تشنج', 'غثيان', 'إقياء', 'إسهال', 'إمساك', 'سعال', 'ضيق تنفس', 'صعوبة في البلع', 'دوار', 'إغماء', 'نزيف', 'طفح جلدي', 'احمرار', 'تورم', 'جفاف', 'تقشر', 'تشقق', 'حكة', 'ألم عند اللمس', 'حساسية للمس', 'حساسية للحرارة', 'حساسية للبرودة', 'حساسية للضوء', 'حساسية للصوت', 'فقدان حاسة التذوق', 'فقدان حاسة الشم', 'قلق', 'اكتئاب', 'صداع', 'إرهاق', 'عصبية', 'توتر', 'اضطراب', 'مشاكل في النوم', 'ارتباك', 'تهيج', 'عدوانية', 'هلوسة', 'أوهام', 'فقدان التركيز', 'صعوبة في التفكير', 'صعوبة في اتخاذ القرارات', 'تغييرات في المزاج', 'سلوكيات غير طبيعية', 'ارتفاع درجة الحرارة', 'قشعريرة', 'حمى', 'قشعريرة', 'إفرازات مهبلية غير طبيعية', 'آلام الحوض', 'نزيف بين الدورات', 'نزيف بعد انقطاع الطمث', 'صعوبة التبول', 'إلحاح بولي', 'سلس البول', 'دم في البول', 'إفرازات قطنية بيضاء من المهبل', 'حرقان عند التبول', 'فرط التبول', 'تبول ليلي', 'ضعف الانتصاب', 'قلة الشهية']
    for keyword in symptoms_keywords:
        if keyword in text:
            score += 1
  
    # Keywords related to causes and risk factors
    causes_and_risk_factors_keywords = ['سبب', 'مسبب', 'عامل', 'يسبب', 'يؤدي إلى', 'يزيد من خطر', 'يقلل من خطر', 'مرض', 'عدوى', 'فيروس', 'بكتيريا', 'فطر', 'طفيلي', 'ورم', 'سرطان', 'خلل', 'اضطراب', 'حالة', 'وراثي', 'تاريخ عائلي', 'غذاء', 'تمارين', 'سمنة', 'تدخين', 'كحول', 'مخدرات', 'إجهاد', 'قلة نوم', 'تلوث', 'مواد كيميائية', 'إشعاع', 'لدغة', 'حشرة', 'إصابة', 'حادث', 'كسر', 'جرح', 'عمر', 'عوامل نفسية', 'ضغط عصبي', 'عوامل اجتماعية اقتصادية', 'فقر', 'انعدام الأمن الغذائي', 'إدمان الكحول والمخدرات', 'التعرض للعنف', 'التعرض للسموم', 'عوامل وراثية', 'طفرات جينية', 'عيوب خلقية', 'خلل التوازن الهرموني', 'أمراض المناعة الذاتية', 'استعداد وراثي', 'استهلاك الأدوية', 'التاريخ الطبي الشخصي', 'أمراض سابقة', 'الحمل', 'الرضاعة الطبيعية', 'سن اليأس', 'الجنس', 'العرق', 'النشاط البدني', 'تعرض أشعة الشمس']
    for keyword in causes_and_risk_factors_keywords:
        if keyword in text:
            score += 1
    
    # Keywords related to complications
    complications_keywords = ['مضاعفات', 'مضاعفة', 'يعقد', 'يؤدي إلى', 'يزيد من خطر', 'إعاقة', 'ضعف', 'فقدان وظيفة', 'اكتئاب', 'قلق', 'ألم مزمن', 'انتشار', 'وفاة', 'يهدد الحياة', 'تلف دائم', 'فشل عضوي', 'غيبوبة', 'عجز دائم', 'تشوهات', 'ندبات', 'التهاب مزمن', 'اضطرابات نفسية', 'اعتمادية على العلاج', 'انتكاس المرض', 'موت الأنسجة', 'نقص المناعة', 'سرطان ثانوي']
    for keyword in complications_keywords:
        if keyword in text:
            score += 1
    
    # Keywords related to diagnosis
    diagnosis_keywords = ['تشخيص', 'تشخيصي', 'يحدد', 'يكشف عن', 'يقيّم', 'تاريخ طبي', 'أعراض', 'فحص جسدي', 'فحص سريري', 'تحليل', 'فحص', 'تصوير', 'أشعة سينية', 'أشعة مقطعية', 'تصوير بالرنين المغناطيسي', 'تحليل دم', 'تحليل بول', 'خزعة', 'تنظير داخلي', 'تخطيط كهربية القلب', 'تخطيط كهربية الدماغ', 'قياس ضغط الدم', 'قياس السكر', 'اختبارات وظائف الكلى', 'اختبارات وظائف الكبد', 'اختبارات الحساسية', 'اختبارات الحمض النووي', 'فحص الحمض النووي', 'فحص جيني']
    for keyword in diagnosis_keywords:
        if keyword in text:
            score += 1
    
    # Keywords related to treatments and drugs
    treatments_and_drugs_keywords = ['علاج', 'علاج طبي', 'دواء', 'جرعة', 'جراحة', 'إشعاع', 'علاج طبيعي', 'علاج إشعاعي', 'علاج كيماوي', 'علاج بالهرمونات', 'علاج بالضوء', 'علاج سلوكي معرفي', 'علاج بالوخز بالإبر', 'علاج بالاسترخاء', 'علاج بالفن', 'علاج بالحمية الغذائية', 'علاج بديل', 'علاج تكميلي', 'جراحة من الحد الأدنى', 'جراحة تنظيرية', 'علاج بالخلايا الجذعية', 'علاج بالجينات', 'العلاج المناعي', 'المضادات الحيوية', 'مضادات الفيروسات', 'مضادات الفطريات', 'مضادات الطفيليات', 'مسكنات الألم', 'خافضات الحرارة', 'مضادات الالتهاب', 'مضادات الا']
    for keyword in treatments_and_drugs_keywords:
        if keyword in text:
            score += 1
    
    # Keywords related to prevention
    prevention_keywords = ['الوقاية', 'التوقي', 'الوقاية من', 'التوقي من', 'تجنب', 'تقليل', 'تحسين', 'الحد من', 'الوقاية الأولية', 'التوعية', 'التثقيف', 'التوجيه', 'النصائح', 'التوجيهات', 'التدابير', 'التدابير الوقائية', 'الإجراءات الوقائية', 'تغيير نمط الحياة', 'النظام الغذائي الصحي', 'ممارسة الرياضة', 'تجنب التدخين', 'التقليل من تناول الكحول', 'التقليل من تناول المخدرات', 'النوم الجيد', 'التقليل من التوتر', 'تجنب التعرض للعوامل الملوثة', 'التقليل من التعرض للإشعاع', 'استخدام وسائل الوقاية', 'التطعيم', 'التطهير', 'التعقيم', 'تنظيف اليدين', 'تنظيف البيئة', 'التغذية السليمة', 'العناية بالصحة النفسية', 'التوجيهات الطبية', 'الفحوصات الدورية', 'الكشف المبكر']
    for keyword in prevention_keywords:
        if keyword in text:
            score += 1
    
    return score

# Apply the score_text function to the 'content' column and update the 'score' column
df['score'] = df['content'].apply(score_text)

# Display the updated DataFrame
df.head()

disease_type                 disease_name  \
0  تسوس الأسنان  امراض الاغشية المخاطية للفم   
1  تسوس الأسنان            امراض التهاب اللب   
2  تسوس الأسنان         عيوب خلقية لجوف الفم   
3    مرض السكري             حساسية الإنسولين   
4  تسوس الأسنان               ساركوما كابوزي   

                                             content  score  
0  تسوس الأسنان\nامراض الاغشية المخاطية للفم\nتغط...     37  
1  تسوس الأسنان\nامراض التهاب اللب\nقد يكون الالت...     37  
2  تسوس الأسنان\nعيوب خلقية لجوف الفم\nيوجد للفم ...     42  
3  مرض السكري\nحساسية الإنسولين\nحتى نهاية سنوات ...     20  
4  تسوس الأسنان\nساركوما كابوزي\nساركوما كابوزي ع...     25

In [48]:
def normalize_score(df, column_name):
    # Find the minimum and maximum scores
    min_score = df[column_name].min()
    max_score = df[column_name].max()
    
    # Normalize the scores between 0 and 10
    df['score'] = (df[column_name] - min_score) * 10 / (max_score - min_score)
    
    return df

# Example usage:
# Assuming df is your DataFrame and 'score' is the column containing scores
# Replace 'score' with the actual column name in your DataFrame
df = normalize_score(df, 'score')
df.head(40)

disease_type                 disease_name  \
0          تسوس الأسنان  امراض الاغشية المخاطية للفم   
1          تسوس الأسنان            امراض التهاب اللب   
2          تسوس الأسنان         عيوب خلقية لجوف الفم   
3            مرض السكري             حساسية الإنسولين   
4          تسوس الأسنان               ساركوما كابوزي   
5          تسوس الأسنان                    جفاف الفم   
6           تساقط الشعر                  تساقط الشعر   
7          تسوس الأسنان                   رائحة الفم   
8         الحمل المنتبذ              الولادة المبكرة   
9         الحمل المنتبذ                      الإجهاض   
10        الحمل المنتبذ              الإجهاض الطبيعي   
11        الحمل المنتبذ                قيء مفرط حملي   
12        الحمل المنتبذ             الإجهاض الإنتاني   
13        الحمل المنتبذ               انفصال المشيمة   
14        الحمل المنتبذ           تلوث السائل السلوي   
15        الحمل المنتبذ                 الحمل الرحوي   
16              الحنجرة                 التهاب الحلق   
17             البواسير                    رتق الشرج   
18        الجهاز الهضمي      الارتجاع المعدي المريئي   
19             البواسير        الناسور في فتحة الشرج   
20        الجهاز الهضمي                   تشمع الكبد   
21        الجهاز الهضمي                    براز دهني   
22        الجهاز الهضمي                    تغوط مدمى   
23        الجهاز الهضمي               التهاب الكبد ب   
24             البواسير                الخراج الشرجي   
25           الإنفلونزا         التهاب الجيوب المزمن   
26        الجهاز الهضمي                   مرض ويلسون   
27        الجهاز الهضمي                  السالمونيلا   
28        الجهاز الهضمي                      الإمساك   
29        الجهاز الهضمي       التهاب القولون التقرحي   
30  آلام الدورة الشهرية                 سرطان المبيض   
31        الجهاز الهضمي                 الفشل الكبدي   
32           الإنفلونزا                 متلازمة داون   
33        الجهاز الهضمي                   سلس البراز   
34        الجهاز الهضمي               نواسير الامعاء   
35        الجهاز الهضمي                تدلي المستقيم   
36        الجهاز الهضمي               انسداد الامعاء   
37        الجهاز الهضمي                  رتق الامعاء   
38        الجهاز الهضمي                   رتق المريء   
39        الجهاز الهضمي                الزحار العصوي   

                                              content     score  
0   تسوس الأسنان\nامراض الاغشية المخاطية للفم\nتغط...  5.384615  
1   تسوس الأسنان\nامراض التهاب اللب\nقد يكون الالت...  5.384615  
2   تسوس الأسنان\nعيوب خلقية لجوف الفم\nيوجد للفم ...  6.153846  
3   مرض السكري\nحساسية الإنسولين\nحتى نهاية سنوات ...  2.769231  
4   تسوس الأسنان\nساركوما كابوزي\nساركوما كابوزي ع...  3.538462  
5   تسوس الأسنان\nجفاف الفم\nيُساعد اللعاب على منع...  5.538462  
6   تساقط الشعر\nتساقط الشعر\nأي شخص يُلاحظ أن شعر...  3.692308  
7   تسوس الأسنان\nرائحة الفم\nيعاني العديد من الأش...  3.384615  
8   الحمل المنتبذ\nالولادة المبكرة\nيستمر الحمل ال...  4.461538  
9   الحمل المنتبذ\nالإجهاض\nالإجهاض هو الفقد التلق...  7.076923  
10  الحمل المنتبذ\nالإجهاض الطبيعي\nيحدث الإجهاض ا...  4.769231  
11  الحمل المنتبذ\nقيء مفرط حملي\nيعد القيء المفرط...  5.230769  
12  الحمل المنتبذ\nالإجهاض الإنتاني\nالإجهاض الإنت...  3.538462  
13  الحمل المنتبذ\nانفصال المشيمة\nيحدث انفصال الم...  2.923077  
14  الحمل المنتبذ\nتلوث السائل السلوي\nالسائل السل...  3.076923  
15  الحمل المنتبذ\nالحمل الرحوي\nيعرف الحمل الرحوي...  3.538462  
16  الحنجرة\nالتهاب الحلق\nالتهاب الحلق يكاد يكون ...  2.307692  
17  البواسير\nرتق الشرج\nيعد رتق الشرج أحد الاضطرا...  3.230769  
18  الجهاز الهضمي\nالارتجاع المعدي المريئي\nمرض ال...  5.230769  
19  البواسير\nالناسور في فتحة الشرج\nيشكل الناسور ...  2.769231  
20  الجهاز الهضمي\nتشمع الكبد\nمرض تشمع الكبد هو ت...  5.384615  
21  الجهاز الهضمي\nبراز دهني\nالبراز الدهني (FAatt...  5.384615  
22  الجهاز الهضمي\nتغوط مدمى\nالتغوط المدمى مصطلح ...  3.230769  
23  الجهاز الهضمي\nالتهاب الكبد ب\nالتهاب الكبد ب ...  5.230769  
24  البواسير\nالخراج الشرجي\nيظهر الخراج الشرجي نت...  1.692308 

In [49]:
import re
import pandas as pd

# Define the basic_cleaning function
def basic_cleaning(text):
    text = str(text)  # Convert to string to handle non-string inputs
    text = text.lower()  # Lowercasing
    text = re.sub(r'{.*?}', '', text)   # Remove CSS code within curly braces
    # Removing all except alphanumeric characters, spaces, and specified characters
    text = re.sub(r'[^\w\s\-\+\*/!()\[\]{}<>]', '', text)
    # Remove HTML tags
    text = re.sub(r'<[^>]+>', '', text)
    # Remove CSS
    text = re.sub(r'<style[^>]*>[\s\S]+?</style>', '', text)
    # Remove '\n' and replace with space
    text = text.replace('\n', ' ')
    # Remove non-Arabic characters and non-Arabic numbers
    text = re.sub(r'[^\u0621-\u064A0-9\s\-\+\*/!\[\]{}<>]', '', text)

    # Remove extra whitespaces
    text = re.sub(r'\s+', ' ', text).strip()
    return text

# Fill any NaN values with an empty string
df.fillna('', inplace=True)

# Display the updated DataFrame
df.head()

disease_type                 disease_name  \
0  تسوس الأسنان  امراض الاغشية المخاطية للفم   
1  تسوس الأسنان            امراض التهاب اللب   
2  تسوس الأسنان         عيوب خلقية لجوف الفم   
3    مرض السكري             حساسية الإنسولين   
4  تسوس الأسنان               ساركوما كابوزي   

                                             content     score  
0  تسوس الأسنان\nامراض الاغشية المخاطية للفم\nتغط...  5.384615  
1  تسوس الأسنان\nامراض التهاب اللب\nقد يكون الالت...  5.384615  
2  تسوس الأسنان\nعيوب خلقية لجوف الفم\nيوجد للفم ...  6.153846  
3  مرض السكري\nحساسية الإنسولين\nحتى نهاية سنوات ...  2.769231  
4  تسوس الأسنان\nساركوما كابوزي\nساركوما كابوزي ع...  3.538462

In [50]:
def tokenize(text):
    return word_tokenize(text)

def remove_stopwords(tokens):
    stop_words = set(stopwords.words('english'))
    return [word for word in tokens if word not in stop_words]

def stem_tokens(tokens):
    stemmer = PorterStemmer()
    return [stemmer.stem(word) for word in tokens]

def lemmatize_tokens(tokens):
    lemmatizer = WordNetLemmatizer()
    return [lemmatizer.lemmatize(word) for word in tokens]

def preprocess_text(df, text_column):
    df['cleaned_text'] = df[text_column].apply(basic_cleaning)
    df['tokens'] = df['cleaned_text'].apply(tokenize)
    df['tokens'] = df['tokens'].apply(remove_stopwords)
    df['stemmed_tokens'] = df['tokens'].apply(lambda x: ' '.join(stem_tokens(x)))
    df['lemmatized_tokens'] = df['tokens'].apply(lambda x: ' '.join(lemmatize_tokens(x)))
    return df

preprocessed_df = preprocess_text(df, 'content')
preprocessed_df.head()

disease_type                 disease_name  \
0  تسوس الأسنان  امراض الاغشية المخاطية للفم   
1  تسوس الأسنان            امراض التهاب اللب   
2  تسوس الأسنان         عيوب خلقية لجوف الفم   
3    مرض السكري             حساسية الإنسولين   
4  تسوس الأسنان               ساركوما كابوزي   

                                             content     score  \
0  تسوس الأسنان\nامراض الاغشية المخاطية للفم\nتغط...  5.384615   
1  تسوس الأسنان\nامراض التهاب اللب\nقد يكون الالت...  5.384615   
2  تسوس الأسنان\nعيوب خلقية لجوف الفم\nيوجد للفم ...  6.153846   
3  مرض السكري\nحساسية الإنسولين\nحتى نهاية سنوات ...  2.769231   
4  تسوس الأسنان\nساركوما كابوزي\nساركوما كابوزي ع...  3.538462   

                                        cleaned_text  \
0  تسوس الأسنان امراض الاغشية المخاطية للفم تغطي ...   
1  تسوس الأسنان امراض التهاب اللب قد يكون الالتها...   
2  تسوس الأسنان عيوب خلقية لجوف الفم يوجد للفم وظ...   
3  مرض السكري حساسية الإنسولين حتى نهاية سنوات ال...   
4  تسوس الأسنان ساركوما كابوزي ساركوما كابوزي عبا...   

                                              tokens  \
0  [تسوس, الأسنان, امراض, الاغشية, المخاطية, للفم...   
1  [تسوس, الأسنان, امراض, التهاب, اللب, قد, يكون,...   
2  [تسوس, الأسنان, عيوب, خلقية, لجوف, الفم, يوجد,...   
3  [مرض, السكري, حساسية, الإنسولين, حتى, نهاية, س...   
4  [تسوس, الأسنان, ساركوما, كابوزي, ساركوما, كابو...   

                                      stemmed_tokens  \
0  تسوس الأسنان امراض الاغشية المخاطية للفم تغطي ...   
1  تسوس الأسنان امراض التهاب اللب قد يكون الالتها...   
2  تسوس الأسنان عيوب خلقية لجوف الفم يوجد للفم وظ...   
3  مرض السكري حساسية الإنسولين حتى نهاية سنوات ال...   
4  تسوس الأسنان ساركوما كابوزي ساركوما كابوزي عبا...   

                                   lemmatized_tokens  
0  تسوس الأسنان امراض الاغشية المخاطية للفم تغطي ...  
1  تسوس الأسنان امراض التهاب اللب قد يكون الالتها...  
2  تسوس الأسنان عيوب خلقية لجوف الفم يوجد للفم وظ...  
3  مرض السكري حساسية الإنسولين حتى نهاية سنوات ال...  
4  تسوس الأسنان ساركوما كابوزي ساركوما كابوزي عبا...

In [52]:
print(preprocessed_df['cleaned_text'][983])

العيون حول الحول أو حول العيون هو حالة لا يلتقي فيها محورا الرؤية في كلتا العينين في نقطة واحدة وقد يظهر الحول عند النظر إلى الأمام أو إلى الجانبين وقد يكون حالة ثابتة مستديمة أو متغيرة في أوقات مختلفة أشكال الحول يتم التمييز عادة بين شكلين أساسيين من الحول 1 الحول التصاحبي وهي الحالة التي تكون فيها زاوية الحول أي مدى انحراف العين ثابتة في كل اتجاهات النظر 2 الحول اللا تصاحبي وهي الحالة التي تختلف فيها زاوية الحول باختلاف اتجاه النظر هذا الشكل قد ينتج عن شلل في واحدة أو أكثر من العضلات التي تتحكم بحركات العين اتجاه انحراف العين يحدد نوع وشكل الحول في حالة القبل أي الحول الداخلي أو الحول الإنسي يكون انحراف العين إلى الداخل باتجاه الأنف في حالة الخزر أي الحول الخارجي أو الحول الوحشي يكون انحراف العين إلى الخارج باتجاه الأذن في حالة الحول الفوقاني أي الحول المتجانس إلى الأعلى يكون انحراف العين نحو الأعلى في حالة الحول التحتاني أي الحول المتجانس إلى الأسفل يكون انحراف العين نحو الأسفل قد يظهر حول العيون في جميع المراحل العمرية رغم أن معظم حالات الحول تظهر في مرحلة الطفولة فالحول الداخلي لد

In [55]:
!pip install tensorflow

^C


In [56]:
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
import tensorflow as tf
from tensorflow.keras.layers import SimpleRNN, Bidirectional, GRU, LSTM, Dense

ModuleNotFoundError: No module named 'tensorflow'

In [ ]:

# Assuming you have already preprocessed your text data and embedded it with TF-IDF
# Adjust the following based on your actual data
max_sequence_length = 100  # Set an appropriate sequence length
num_features = 300  # Number of features after embedding

# Split data into features (X) and target (y)
X = df['cleaned_text']  # Assuming 'content' contains preprocessed text features
y = df['score']

# Split into train and test sets
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

# Create a simple RNN model
model_rnn = build_rnn_model(input_shape=(max_sequence_length, num_features), num_classes=1)
model_rnn.compile(optimizer='adam', loss='mean_squared_error', metrics=['mae'])
model_rnn.fit(X_train, y_train, epochs=10, batch_size=32, validation_data=(X_test, y_test))

# Create a bidirectional RNN model
model_bidirectional_rnn = build_bidirectional_rnn_model(input_shape=(max_sequence_length, num_features), num_classes=1)
model_bidirectional_rnn.compile(optimizer='adam', loss='mean_squared_error', metrics=['mae'])
model_bidirectional_rnn.fit(X_train, y_train, epochs=10, batch_size=32, validation_data=(X_test, y_test))

# Create a GRU model
model_gru = build_gru_model(input_shape=(max_sequence_length, num_features), num_classes=1)
model_gru.compile(optimizer='adam', loss='mean_squared_error', metrics=['mae'])
model_gru.fit(X_train, y_train, epochs=10, batch_size=32, validation_data=(X_test, y_test))

# Create an LSTM model
model_lstm = build_lstm_model(input_shape=(max_sequence_length, num_features), num_classes=1)
model_lstm.compile(optimizer='adam', loss='mean_squared_error', metrics=['mae'])
model_lstm.fit(X_train, y_train, epochs=10, batch_size=32, validation_data=(X_test, y_test))
